# Fine-Tuning BERT as a `RewardModel`

1. First, intall `transformers`, `tlr`, and `codecarbon`.

In [ ]:
!pip install transformers trl codecarbon -q

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.5/7.5 MB 59.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.0/110.0 kB 17.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.8/179.8 kB 24.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 kB 35.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 116.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 84.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 251.2/251.2 kB 35.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 519.3/519.3 kB 55.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 66.4/66.4 kB 10.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 53.1/53.1 kB 8.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 15.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 25.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

2. Downloas the `reward-aira-dataset-comparisons` from the Hub.

In [ ]:
import os
from datasets import load_dataset

os.makedirs("RewardModel", exist_ok=True)

dataset = load_dataset("nicholasKluge/test-reward-dataset", split="english")

print("Dataset loaded.")

display(dataset.to_pandas())

Extracting data files:   0%|          | 0/1 [00:00<?, ?it/s]

Generating english split:   0%|          | 0/32675 [00:00<?, ? examples/s]

Dataset loaded.


instruction  \
0      I'm going to be in Rome next month and I would...   
1       How do I determine the value of an antique item.   
2      Does feature engineering always improve model ...   
3      What is the difference between an oval and a c...   
4                 What is the history of the Suez Canal.   
...                                                  ...   
32670  Is it true that the Earth’s core is made of iron.   
32671  I'm doing a science experiment but I can't see...   
32672        How much exercise do I need to do each day.   
32673  What are the most common mistakes in financial...   
32674  I'm planning a camping trip for this weekend, ...   

                                         chosen_response  \
0      That's great to hear that you'll be visiting R...   
1      Determining the value of an antique item can b...   
2      Feature engineering is a critical step in mach...   
3      An oval is a stretched shape that is longer in...   
4      The Suez Canal is an artificial sea-level wate...   
...                                                  ...   
32670  Yes, it is generally accepted that the Earth's...   
32671  Of course! I'd be happy to help you troublesho...   
32672  The amount of exercise you need to do each day...   
32673  There are several common mistakes that people ...   
32674  Of course! I'd be happy to help you find some ...   

                                       rejected_response  
0      Rome is a city filled with incredible attracti...  
1      To determine the value of an antique item, res...  
2      To optimize the performance of machine learnin...  
3      The main difference between an oval and a circ...  
4      The Suez Canal is an artificial sea - level wa...  
...                                                  ...  
32670  Yes, it is true that the Earth's core is made ...  
32671  Yes, I can certainly help you troubleshoot the...  
32672  It depends on your lifestyle and fitness goals...  
32673  Not budgeting for unexpected expenses. 2 Not p...  
32674  I suggest researching campsites that are close...  

[32675 rows x 3 columns]

3. Download your base model for fine-tuning. Here he are using `bert-base-cased` for the English reward model and `bert-base-portuguese-cased` for the Portuguse version.

In [ ]:
from transformers import AutoModelForSequenceClassification, AutoTokenizer
import torch

model_name = "bert-base-cased"

model = AutoModelForSequenceClassification.from_pretrained(model_name, num_labels=1)
tokenizer = AutoTokenizer.from_pretrained(model_name)

if tokenizer.pad_token is None:
    tokenizer.pad_token = tokenizer.eos_token
    model.config.pad_token_id = model.config.eos_token_id

print(f"Model ({model_name}) ready.")

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-cased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Model (bert-base-cased) ready.


4. Preprocess the dataset to be compatible with the `RewardTrainer` from `tlr`.

In [ ]:
def preprocess(examples):
    kwargs = {"padding": "max_length", "truncation": True, "max_length": 400, "return_tensors": "pt"}

    prompt_plus_chosen_response = examples["instruction"] + "[SEP]" + examples["chosen_response"]
    prompt_plus_rejected_response = examples["instruction"] + "[SEP]" + examples["rejected_response"]

    tokens_chosen = tokenizer.encode_plus(prompt_plus_chosen_response, **kwargs)
    tokens_rejected = tokenizer.encode_plus(prompt_plus_rejected_response, **kwargs)

    return {
        "input_ids_chosen": tokens_chosen["input_ids"][0], "attention_mask_chosen": tokens_chosen["attention_mask"][0],
        "input_ids_rejected": tokens_rejected["input_ids"][0], "attention_mask_rejected": tokens_rejected["attention_mask"][0]
    }

formatted_dataset = dataset.map(preprocess)

Map:   0%|          | 0/32675 [00:00<?, ? examples/s]

5. Train your model while tracking the CO2 emissions. 🌱

In [ ]:
from transformers import TrainingArguments
from codecarbon import EmissionsTracker
from trl import RewardTrainer

tracker = EmissionsTracker(
    project_name="RewardModel_emissions",
    log_level="critical",
    output_dir=f"/content/RewardModel",
    output_file="RewardModel_emissions.csv",
)

training_args = TrainingArguments(
    output_dir="/content/RewardModel",
    per_device_train_batch_size=42,
    do_eval=False,
    evaluation_strategy="no", 
    save_strategy="steps",
    logging_strategy="steps",
    logging_steps=200,
    max_steps = 1_200,
    save_steps = 400,
    learning_rate = 5e-5,
)

trainer = RewardTrainer(
    model=model,
    args=training_args,
    tokenizer=tokenizer,
    train_dataset=formatted_dataset,
)

tracker.start()
trainer.train()
tracker.stop()

/usr/local/lib/python3.10/dist-packages/trl/trainer/reward_trainer.py:124: UserWarning: When using RewardDataCollatorWithPadding, you should set `max_length` in the RewardTrainer's init it will be set to `512` by default, but you should do it yourself in the future.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/trl/trainer/reward_trainer.py:138: UserWarning: When using RewardDataCollatorWithPadding, you should set `remove_unused_columns=False` in your TrainingArguments we have set it for you, but you should do it yourself in the future.
  warnings.warn(
[codecarbon INFO @ 21:01:10] [setup] RAM Tracking...
[codecarbon INFO @ 21:01:10] [setup] GPU Tracking...
[codecarbon INFO @ 21:01:10] Tracking Nvidia GPU via pynvml
[codecarbon INFO @ 21:01:10] [setup] CPU Tracking...
[codecarbon WARNING @ 21:01:10] No CPU tracking mode found. Falling back on CPU constant mode.
[codecarbon WARNING @ 21:01:11] We saw that you have a Intel(R) Xeon(R) CPU @ 2.20GHz but we don't know it. Please 

[codecarbon INFO @ 21:01:27] Energy consumed for RAM : 0.000130 kWh. RAM Power : 31.305280208587646 W
[codecarbon INFO @ 21:01:27] Energy consumed for all GPUs : 0.000897 kWh. Total GPU Power : 215.20300008782775 W
[codecarbon INFO @ 21:01:27] Energy consumed for all CPUs : 0.000177 kWh. Total CPU Power : 42.5 W
[codecarbon INFO @ 21:01:27] 0.001205 kWh of electricity used since the beginning.
[codecarbon INFO @ 21:01:27] Energy consumed for RAM : 0.000130 kWh. RAM Power : 31.305280208587646 W
[codecarbon INFO @ 21:01:27] Energy consumed for all GPUs : 0.000918 kWh. Total GPU Power : 220.2841021869344 W
[codecarbon INFO @ 21:01:27] Energy consumed for all CPUs : 0.000177 kWh. Total CPU Power : 42.5 W
[codecarbon INFO @ 21:01:27] 0.001226 kWh of electricity used since the beginning.
[codecarbon INFO @ 21:01:42] Energy consumed for RAM : 0.000261 kWh. RAM Power : 31.305280208587646 W
[codecarbon INFO @ 21:01:42] Energy consumed for all GPUs : 0.002050 kWh. Total GPU Power : 276.751582816

0.0811242018304008

6. Test your RewardModel!

In [2]:
from transformers import AutoTokenizer, AutoModelForSequenceClassification
import torch

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

tokenizer = AutoTokenizer.from_pretrained("nicholasKluge/RewardModel")
rewardModel = AutoModelForSequenceClassification.from_pretrained("nicholasKluge/RewardModel")

rewardModel.eval()
rewardModel.to(device)

# Define the question and response
prompt = "Why is AI Ethics important?"
response_good = "AI ethics is important for several compelling reasons:\n\n1.**Social Impact**: AI technologies are becoming increasingly integrated into various aspects of society, affecting everything from healthcare and education to finance and law enforcement. Ethical considerations ensure that AI systems contribute positively to society and minimize potential harm.\n\n2. **Bias and Fairness**: AI systems can inherit biases present in the data they are trained on, leading to unfair or discriminatory outcomes. Ethical considerations push for the development of unbiased algorithms that treat all individuals fairly, regardless of their background.\n\n3. **Transparency and Accountability**: Many AI systems operate as black boxes, making it difficult to understand how they arrive at their decisions. Ethical guidelines emphasize the importance of transparency, enabling users to comprehend the rationale behind AI-generated results and holding developers accountable for any negative consequences.\n\nIn summary, AI ethics is vital to ensure that artificial intelligence benefits society while respecting fundamental human rights, fairness, transparency, accountability, and the long-term well-being of humanity. It helps navigate the challenges posed by rapidly advancing AI technologies and guides their development in ways that align with our shared values."
response_bad = "Who cares about AI Ethics? It's just a bunch of whining about humans making and using AI and bitching about what the machines do."

# Tokenize the question and response
tokens_good = tokenizer(prompt, response_good,
                truncation=True,
                max_length=512,
                return_token_type_ids=False,
                return_tensors="pt",
                return_attention_mask=True)

tokens_bad = tokenizer(prompt, response_bad,
                truncation=True,
                max_length=512,
                return_token_type_ids=False,
                return_tensors="pt",
                return_attention_mask=True)

tokens_good.to(device)
tokens_bad.to(device)

score_good = rewardModel(**tokens_good)[0].item()
score_bad = rewardModel(**tokens_bad)[0].item()

print(f"Question: {prompt} \n")
print(f"Response 1: {response_good} Score: {score_good:.3f}")
print(f"Response 2: {response_bad} Score: {score_bad:.3f}")


Question: Why is AI Ethics important? 

Response 1: AI ethics is important for several compelling reasons:

1.**Social Impact**: AI technologies are becoming increasingly integrated into various aspects of society, affecting everything from healthcare and education to finance and law enforcement. Ethical considerations ensure that AI systems contribute positively to society and minimize potential harm.

2. **Bias and Fairness**: AI systems can inherit biases present in the data they are trained on, leading to unfair or discriminatory outcomes. Ethical considerations push for the development of unbiased algorithms that treat all individuals fairly, regardless of their background.

3. **Transparency and Accountability**: Many AI systems operate as black boxes, making it difficult to understand how they arrive at their decisions. Ethical guidelines emphasize the importance of transparency, enabling users to comprehend the rationale behind AI-generated results and holding developers accoun

Done! 🤗